In [11]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
    
    conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)
    
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
    
    conv2 = tf.layers.conv2d(inputs=pool1, filters=64, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)
    
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
    
    pool2_flat = tf.reshape(pool2, [-1, 7*7*64])
    
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    logits = tf.layers.dense(inputs=dropout, units=10)
    
    predictions = {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

def main(unused_argv):
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")
    
    tensors_to_log ={"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)
    
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
    
    mnist_classifier.train(input_fn=train_input_fn, steps=20000, hooks=[logging_hook])

  # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)


if __name__ == "__main__":
  tf.app.run()
    

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-1
INFO:tensorflow:Saving checkpoints for 2 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:loss = 2.30406, step = 2
INFO:tensorflow:probabilities = [[ 0.10085002  0.11188058  0.09171999  0.10790462  0.10152049  0.09043639
   0.09733468  0.09693253  0.09933589  0.10208478]
 [ 0.09151481  0.10358529  0.07720801  0.1159526   0.11526693  0.08889569
   0.10805388  0.09007086  0.09421512  0.11523676]
 [ 0.09817179  0.10233463  0.09446198  0.10637178  0.10039455  0.08714809
   0.1086245   0.08477397  0.10844816  0.10927057]
 [ 0.08991575  0.10426577  0.09007031  0.100691    0.11630703  0.09876505
   0.0

INFO:tensorflow:probabilities = [[ 0.09180893  0.11226975  0.07475612  0.11183579  0.10688211  0.08683395
   0.09880952  0.09568236  0.0961336   0.12498784]
 [ 0.08479232  0.10348025  0.09049736  0.09322538  0.11877315  0.09392909
   0.09662936  0.09738778  0.10709524  0.11419001]
 [ 0.09670191  0.11833429  0.0905393   0.09854919  0.11420282  0.08833168
   0.0881511   0.08293071  0.09394293  0.12831604]
 [ 0.08944447  0.11394768  0.08622079  0.11278789  0.10366417  0.08331747
   0.10654164  0.09835678  0.09668188  0.10903721]
 [ 0.09858927  0.09606998  0.08499955  0.11172328  0.10714696  0.09386688
   0.11497841  0.0863758   0.08975971  0.11649016]
 [ 0.09536826  0.10927414  0.0925272   0.09262308  0.1038077   0.09191447
   0.10054131  0.10865919  0.09874977  0.1065348 ]
 [ 0.08891065  0.10609961  0.0897381   0.10633193  0.09316379  0.08814636
   0.11145218  0.11074601  0.09162391  0.11378743]
 [ 0.09259126  0.09824198  0.08052173  0.11568893  0.10724531  0.09283908
   0.10733685  0.10

INFO:tensorflow:global_step/sec: 5.09042
INFO:tensorflow:loss = 2.26848, step = 102 (19.646 sec)
INFO:tensorflow:probabilities = [[ 0.10800116  0.10884947  0.08517019  0.10478895  0.09233629  0.10172144
   0.10912523  0.09504811  0.08712914  0.10783011]
 [ 0.09521152  0.10076704  0.07991311  0.11117649  0.1025107   0.08490922
   0.10925958  0.11346047  0.09416804  0.10862384]
 [ 0.09996165  0.08573621  0.08726685  0.11625939  0.09265189  0.09944879
   0.10098328  0.10418577  0.09863874  0.1148675 ]
 [ 0.09913699  0.11538032  0.10047612  0.1050313   0.09795853  0.08413929
   0.10509386  0.08311889  0.0992767   0.11038801]
 [ 0.11174147  0.10765883  0.08433659  0.10232878  0.10478928  0.0951201
   0.09963239  0.09977794  0.08424198  0.11037269]
 [ 0.09349988  0.10949853  0.09172151  0.12117483  0.09600608  0.09249605
   0.10632235  0.09866125  0.08645552  0.10416394]
 [ 0.09187842  0.10560038  0.09642076  0.10558135  0.10850823  0.09548783
   0.10371792  0.09132313  0.10041664  0.1010653

INFO:tensorflow:probabilities = [[ 0.08733421  0.11105306  0.08107205  0.09720035  0.09920437  0.09783376
   0.11655851  0.09130488  0.10804873  0.11039016]
 [ 0.08270799  0.10420635  0.0929153   0.10950723  0.09605947  0.0883992
   0.10598265  0.10508251  0.09657595  0.11856328]
 [ 0.10251813  0.10349619  0.09263527  0.08829527  0.09981625  0.10336341
   0.10502931  0.08985161  0.1132484   0.10174615]
 [ 0.08694045  0.10006053  0.08519716  0.11856239  0.09104941  0.08313121
   0.09920139  0.10425226  0.10441402  0.1271912 ]
 [ 0.09330934  0.09907491  0.09399805  0.10843061  0.09964728  0.07820559
   0.11407244  0.09756657  0.10262585  0.11306935]
 [ 0.09586447  0.10325782  0.08846618  0.10493388  0.09772784  0.08537998
   0.0969935   0.09499022  0.12192248  0.11046364]
 [ 0.08368804  0.09507853  0.08215389  0.11251078  0.10769706  0.09438102
   0.11640701  0.09716819  0.11225258  0.09866284]
 [ 0.09409142  0.10773629  0.09422822  0.11443514  0.09664445  0.09765784
   0.09572688  0.094

INFO:tensorflow:global_step/sec: 4.96797
INFO:tensorflow:loss = 2.2861, step = 202 (20.129 sec)
INFO:tensorflow:probabilities = [[ 0.09439454  0.10317834  0.08638505  0.10790318  0.10607973  0.08732969
   0.1012148   0.0975305   0.10280462  0.11317957]
 [ 0.08668824  0.10075209  0.08197891  0.10511725  0.10849723  0.09587285
   0.1057703   0.10188215  0.0993679   0.11407306]
 [ 0.09219314  0.11651134  0.09277397  0.10509852  0.09963322  0.09616392
   0.10340574  0.09494335  0.09561853  0.10365838]
 [ 0.10014272  0.09350798  0.09223384  0.10745272  0.10021204  0.10053718
   0.10020164  0.10266501  0.10390779  0.09913906]
 [ 0.09509182  0.09904856  0.09328032  0.11865475  0.09344782  0.10535016
   0.11084856  0.08452138  0.10130396  0.09845264]
 [ 0.09525096  0.10355222  0.09380025  0.11561345  0.10448711  0.07928655
   0.09764389  0.09580588  0.10124802  0.11331166]
 [ 0.10180609  0.11071388  0.08943054  0.11501165  0.07834885  0.10491616
   0.09868568  0.09618878  0.09436308  0.1105353

...

INFO:tensorflow:global_step/sec: 5.52407
INFO:tensorflow:loss = 0.15297, step = 19902 (18.102 sec)
INFO:tensorflow:probabilities = [[ 0.00023329  0.99375397  0.00045602  0.00093943  0.0012496   0.00013716
   0.00032839  0.00189891  0.00047339  0.00052991]
 [ 0.00001579  0.00000168  0.0001001   0.99684983  0.00000094  0.00280993
   0.00000017  0.00000004  0.00012062  0.00010089]
 [ 0.0002758   0.98376667  0.00230412  0.0005114   0.00142974  0.00037406
   0.00135413  0.00651872  0.00236978  0.0010956 ]
 [ 0.00000327  0.00000228  0.00008104  0.00000137  0.00001959  0.00005691
   0.99929667  0.00000005  0.00053824  0.00000054]
 [ 0.00009164  0.00001397  0.00005291  0.00013446  0.90040296  0.00244287
   0.00001582  0.01723515  0.00024154  0.07936864]
 [ 0.00003393  0.97086918  0.00108347  0.00193975  0.00154187  0.00004189
   0.00016421  0.02320704  0.00085084  0.0002678 ]
 [ 0.99982375  0.00000001  0.00000465  0.00000003  0.00000178  0.00000199
   0.00007078  0.00008538  0.00000009  0.0000

INFO:tensorflow:probabilities = [[ 0.00002915  0.00000497  0.0000117   0.00047067  0.00003439  0.99883693
   0.00022569  0.00000844  0.00022875  0.00014925]
 [ 0.00316155  0.00758741  0.00297716  0.01012997  0.0367662   0.00926633
   0.87741703  0.0016152   0.04668337  0.00439581]
 [ 0.0000005   0.00000001  0.00000014  0.00008818  0.00000304  0.00000006
   0.          0.9998368   0.00000268  0.00006848]
 [ 0.00023681  0.00000207  0.00017671  0.00107729  0.21305971  0.00066583
   0.00015501  0.03982626  0.0049885   0.73981184]
 [ 0.00000232  0.00000023  0.00000003  0.00002114  0.00000061  0.99861133
   0.00000981  0.00000157  0.00134582  0.00000709]
 [ 0.9984163   0.00001844  0.00009566  0.00001533  0.00001918  0.00031243
   0.001063    0.00001347  0.00003829  0.00000784]
 [ 0.00073353  0.00005584  0.00035984  0.03008262  0.00008784  0.95551115
   0.00279157  0.00001149  0.01030943  0.00005663]
 [ 0.03273816  0.10433684  0.00202686  0.03075907  0.0130102   0.07960777
   0.63240588  0.00

INFO:tensorflow:Saving checkpoints for 20001 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.102729.
INFO:tensorflow:Starting evaluation at 2018-05-20-16:38:32
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20001
INFO:tensorflow:Finished evaluation at 2018-05-20-16:38:38
INFO:tensorflow:Saving dict for global step 20001: accuracy = 0.9685, global_step = 20001, loss = 0.104851
{'accuracy': 0.96850002, 'loss': 0.10485079, 'global_step': 20001}


SystemExit: 

/Users/ritchevy/anaconda3/envs/tensorflow-sess/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2971: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
